In [54]:
import sys
import os
import datetime as dt
from pathlib import Path
from collections import OrderedDict
import math
from shutil import copyfile
import json

import requests
import gtfstk as gt
#from highcharts import Highchart 

DIR = Path('..')
sys.path.append(str(DIR))

%load_ext autoreload
%autoreload 2

import gtfsrtk as gr

DATA_DIR = DIR/'data'

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [57]:
# From https://gist.github.com/StevenMaude/a7e3ee58c91794b4759075ba5d04708d
from google.protobuf import json_format
from google.transit import gtfs_realtime_pb2


def pb_to_json(pb_path):
    feed = gtfs_realtime_pb2.FeedMessage()

    with Path(pb_path).open('rb') as src:
        feed.ParseFromString(src.read())

    return json.loads(json_format.MessageToJson(feed))


def main():
    filenames = glob.glob('*.pb')
    for filename in filenames:
        print("Converting file:", filename)
        pb_as_json = convert_pb_to_json(filename)
        json_filename = filename.replace('.pb', '.json')
        with open(json_filename, 'w') as f:
            f.write(pb_as_json)


In [58]:
path = DATA_DIR/'tripUpdates.pb'
pb_to_json(path)



{'entity': [{'id': '2014-11-30:CXX:L019:7062',
   'tripUpdate': {'stopTimeUpdate': [{'arrival': {'delay': 0,
       'time': '1417386840'},
      'departure': {'delay': 19, 'time': '1417386859'},
      'stopId': '36992',
      'stopSequence': 1},
     {'arrival': {'delay': -19, 'time': '1417387001'},
      'departure': {'delay': -19, 'time': '1417387001'},
      'stopId': '46130',
      'stopSequence': 3},
     {'arrival': {'delay': -12, 'time': '1417387068'},
      'departure': {'delay': -12, 'time': '1417387068'},
      'stopId': '45551',
      'stopSequence': 4},
     {'arrival': {'delay': -50, 'time': '1417387090'},
      'departure': {'delay': -50, 'time': '1417387090'},
      'stopId': '41317',
      'stopSequence': 5},
     {'arrival': {'delay': -33, 'time': '1417387167'},
      'departure': {'delay': -33, 'time': '1417387167'},
      'stopId': '33187',
      'stopSequence': 6},
     {'arrival': {'delay': -59, 'time': '1417387201'},
      'departure': {'delay': -59, 'time': '1417

In [18]:
# Build a function to get GTFSR trip update feeds
api_key = os.environ['AT_KEY']
url = 'https://api.at.govt.nz/v2/public/realtime/?'#tripupdates?'
headers = {
  'Ocp-Apim-Subscription-Key': api_key,
  }
params = {
  'callback': '',
  'tripid': '',
  'vehicleid': '',
  }    

#r = requests.get(url, headers=headers, params=params)
feed = gtfs_realtime_pb2.FeedMessage()
feed.ParseFromString(r.content)


DecodeError: Error parsing message

In [ ]:
t = gr.get_timestamp(feed)
print(t)
gr.extract_delays(feed)

In [ ]:
# Create augmented stop times

gtfsr_dir = DATA_DIR/'test_gtfsr'
gtfsr_feeds = []
for f in gtfsr_dir.iterdir():
    with f.open() as src:
        gtfsr_feeds.append(json.load(src))
gtfs_feed = gt.read_gtfs(DATA_DIR/'test_gtfs.zip', dist_units_in='km') # Good from 20160519
date = '20160519'

ast = build_augmented_stop_times(gtfsr_feeds, gtfs_feed, date)

tid = '14005028723-20160512154122_v40.34'
ast[ast['trip_id'] == tid]

In [ ]:
# Fill null delays

f = interpolate_delays(ast, dist_threshold=1)
f[f['trip_id'] == tid]
